# Bernstein-Vazirani Algorithm

1. [Bernstein-Vazirani Algorithm](#bva)
2. [Simon's Algorithm](#simon) 
3. [The Algorithms so far](#alg)
4. [Noise Models](#em)

## 1. Bernstein-Vazirani Algorithm<a id='bva'></a>

### The problem

Let the function $f$ be an oracle, which takes a string of bits as inputs and returns either $0$ or $1$:

$$ f: \{0,1\}^n \rightarrow \{ 0,1 \}$$

$f(x)$ is guaranteed to return a bitwise product of the input $x$ with a string $s$, i.e. given $x$, 
$$ f(x) = s \cdot x (\mod 2)$$

The goal of this algorithm is to **find $s$.**

### The classical solution

Classically, the most efficient method to find the secret string is by evaluating the function $n$ times with the input values $x = 2^i$ for all $i \in \{ 0 , 1 , . . . , n − 1 \}$

$$\begin{aligned}f(1000\cdots 0_{n})&=s_{1}\\f(0100\cdots 0_{n})&=s_{2}\\f(0010\cdots 0_{n})&=s_{3}\\&\,\,\,\vdots \\f(0000\cdots 1_{n})&=s_{n}\\\end{aligned}$$

In contrast to the classical solution, which needs at least $n$ queries of the function to find $s$, only one is required using quantum computing.

### The quantum solution

![BV](https://qiskit.org/textbook/ch-algorithms/images/bv1.png)

The algorithm has four main parts.

The initial state is:  $ |0\rangle ^{\otimes n+1}$

1. **Initialize the first $n$ qubits in the state $|0 \rangle$ and the last qubit in the state $|1\rangle$.** In Qiskit, all qubits are initialized in the state $|0\rangle$, so the first qubits remain unchanged. For the last qubit, we initialize it to state $|1\rangle$ by applying an $X$ gate.

$$ |0\rangle^{\otimes n} \otimes |1 \rangle$$

2. **Apply Hadamard gates to all qubits.**

Consider the first $n$ qubits: 

$$ \frac{1}{\sqrt{2^n}} \sum_{x=0}^{2^n-1}{|x\rangle} $$

3. **Build the box containing the secret number (also known as an "oracle").** We will build it as a function that computes $s \cdot x \mod 2$  by applying $CX$ gates from the first $n$ qubits onto the last qubit whenever there is a $1$ in the secret number. We will do this in reverse order, meaning that there will be a $CX$ gate from the $n$th qubit to the last qubit if the first bit of the secret number is $1$.

The oracle applies the transformation:
$$ |x \rangle \rightarrow (-1)^{f(x)} |x\rangle$$

Therefore, the superposition transforms into:
$$ \frac{1}{\sqrt{2^n}} \sum_{x=0}^{2^n-1}{(-1)^{f(x)}|x\rangle} $$

4. **Measure the first $n$ qubits in the Bell basis.** This means applying Hadamard gates to the first $n$ qubits again before applying measurements.

With the Hadamard: 
* For qubits where $s_i = 1$, the qubit state $| -\rangle$ converts to $|1\rangle$;
* For qubits where $s_i = 0$, the qubit state $| +\rangle$ converts to $|0\rangle$;

The algorithm may be represented by:

$ |0\rangle ^{\otimes n} \xrightarrow{H^{\otimes n}} \frac{1}{\sqrt{2^n}} \sum_{x\in \{0,1\}^n}{|x\rangle} \xrightarrow{U_f} \frac{1}{\sqrt{2^n}} \sum_{x\in \{0,1\}^n}{(-1)^{f(x)}|x\rangle} \xrightarrow{H^{\otimes n}} \frac{1}{\sqrt{2^n}} \sum_{x\in \{0,1\}^n}{(-1)^{f(x) + x \cdot y}|y\rangle} = |s\rangle  $

For a particular $y$:

$\frac{1}{2^n} \sum_{x\in \{0,1\}^n}{(-1)^{f(x) + x \cdot y}} = 
\frac{1}{2^n} \sum_{x\in \{0,1\}^n}{(-1)^{x \cdot s + x \cdot y}} = 
\frac{1}{2^n} \sum_{x\in \{0,1\}^n}{(-1)^{x \cdot ( s \otimes y)}} = 1 
\mbox{ if } s \otimes y = \overrightarrow{0}, 0 \mbox{ otherwise}$

In [ ]:
# initialization
import matplotlib.pyplot as plt
import numpy as np
%matplotlib inline
import math
from math import pi

# importing Qiskit
from qiskit import Aer
from qiskit_ibm_provider import IBMProvider
from qiskit import QuantumCircuit, ClassicalRegister, QuantumRegister, transpile, assemble, execute

# import basic plot tools
from qiskit.visualization import plot_histogram

Let the hidden binary string $s$ be '011':

In [ ]:
s = '011'  

In [ ]:
n = 3 # number of qubits used to represent s

# We need a circuit with n qubits, plus one auxiliary qubit
# Also need n classical bits to write the output to
qr = QuantumRegister(n+1)
cr = ClassicalRegister(n)
bv_circuit = QuantumCircuit(qr, cr)

# put auxiliary in state |1>
bv_circuit.x(qr[n])

# Apply Hadamard gates to all qubits
bv_circuit.h(qr)
    
# Apply barrier 
bv_circuit.barrier()

# Apply the inner-product oracle
# reverse s to fit qiskit's qubit ordering or explain your results
bv_circuit.cx(qr[0], qr[n])
bv_circuit.cx(qr[1], qr[n])
        
# Apply barrier 
bv_circuit.barrier()

#Apply Hadamard gates after querying the oracle
for i in range(n):
    bv_circuit.h(qr[i])

# Measurement
for i in range(n):
    bv_circuit.measure(qr[i], cr[i])

bv_circuit.draw(output='mpl')


In [ ]:
# use local simulator
aer_sim = Aer.get_backend('aer_simulator')
shots = 1024
results = aer_sim.run(bv_circuit).result()
answer = results.get_counts()

plot_histogram(answer)

<div class="alert alert-block alert-warning">
    
**Exercise**   Modify the implementation for **any string $s$**. Are the results what you expect? Explain. 
    
</div>

In [ ]:
# number of qubits used to represent s

# We need a circuit with n qubits, plus one auxiliary qubit
# Also need n classical bits to write the output to


# put auxiliary in state |1>

# Apply Hadamard gates to all qubits
    
# Apply barrier 

# Apply the inner-product oracle
# reverse s to fit qiskit's qubit ordering or explain your results
# inverter s

        
# Apply barrier 

#Apply Hadamard gates after querying the oracle

# Measurement


In [ ]:
# use local simulator
aer_sim = Aer.get_backend('aer_simulator')
shots = 1024
qobj = assemble(bv_circuit)
results = aer_sim.run(qobj).result()
answer = results.get_counts()

plot_histogram(answer)

### References:
* [Qiskit Bernstein-Vazirani Algorithm](https://learn.qiskit.org/course/ch-algorithms/bernstein-vazirani-algorithm)
* [original Paper](https://epubs.siam.org/doi/10.1137/S0097539796300921)

## 2. Simon's Algorithm <a id='simon'></a>

### The problem

Let $f$ be an oracle $f:x \in \{0,1\}^n \rightarrow \{0,1\}^n$, that guaranteis $f$ to be either one-to-one($1:1$) or two-to-one (2:1), where:
* a one-to-one function:maps one unique input to every unique output, e.g. $f(1) \rightarrow 1, \quad f(2) \rightarrow 2, \quad f(3) \rightarrow 3, \quad f(4) \rightarrow 4$
* and a two-to-one function maps two inputs to every unique output, e.g. $f(1) \rightarrow 1, \quad f(2)\rightarrow 2, \quad f(3)\rightarrow 1, \quad f(4)\rightarrow 2 \quad$

To find if the function is one-to-one or two-to-one, one needs to express this guarantee in terms of a secret bit string $s$. For some $s \in \{0,1\}^n$, for all $x_1, x_2 \in \{0,1\}^n$,

$ f(x_1)=f(x_2)$ if and only if $x_1 \otimes x_2\in \{0^n,s\}$

where $\otimes$ denotes a bitwise XOR. 

Note that $a\otimes b =0^n$ if and only if $a=b$, 
and for $x_1$ and $s$ in $x_1 \otimes x_2 =s$ , $x_2$ is unique (not equal to $x_1$) if and only if $s \neq 0^n$. 
Therefore, $f$ is two-to-one when $s\neq 0^n$, and one-to-one when $s=0^n$. 

Morever, $x_1 \otimes x_2=s$ implies $x_2= s \otimes x_1$, so $f$ is periodic: $f(x_1)=f(x_2) = f(x_1\otimes s)$ 

### The classical solution

In the classical solution all we can do is to check the values of $x$ until we find a repeated output, i.e. $f(x_i) =f(x_j)$, which allows to calculate $s$. 

After we called the function $m$ times, we compared $m(m-1)/2$ pairs. 

One needs $\frac{1}{2} m(m-1) \sim 2^n$ to ensure a reasonable chance of success. Therefore the complexity is exponential in the number of bits $n$, i.e. $m=O(2^{\frac{n}{2}})$.

### The quantum solution

![Simon](https://qiskit.org/textbook/ch-algorithms/images/simon_steps.png)

1. Two n-qubit input registers are initialized to the zero state: 

$$|\psi_1\rangle=|0\rangle\otimes n|0\rangle\otimes n$$

2. Apply a Hadamard transform to the first register: 

$$|\psi_2⟩=\frac{1}{\sqrt{2^n}}\sum_{x\in\{0,1\}^n}|x\rangle|0\rangle^{\otimes n}$$

3. Apply the query function $Q_f$:
$$|\psi_3\rangle=\frac{1}{\sqrt{2^n}}\sum_{x\in\{0,1\}^n}{|x\rangle|f(x)\rangle}$$

4. Measure the second register. A specific value of $f(x)$ will be observed. Because of the setting of the problem, the observed value $f(x)$ could correspond to two possible inputs: $x$ and $y=x\otimes b$. Therefore the first register becomes: 
$$|\psi_4⟩=\frac{1}{\sqrt{2}}(|x\rangle+|y\rangle)$$
where we omitted the second register since it has been measured.

5. Apply Hadamard on the first register: 
$$|\psi_5⟩=\frac{1}{\sqrt{2^{n+1}}}\sum_{z\in\{0,1\}^n}{[(−1)^{x\cdot z}+(−1)^{y\cdot z}]|z\rangle}$$

6. Measuring the first register will give an output only if: 
$$(−1)x\cdot z=(−1)y\cdot z$$
which means: 
$$x\cdot z=y\cdot z $$
$$x\cdot z=(x\otimes b)\cdot z$$
$$x\cdot z=x\cdot z\otimes b\cdot z$$
$$b\cdot z=0 (\mod 2)$$ 

A string $z$ will be measured, whose inner product with $b=0$. Thus, repeating the algorithm $ \approx n$ times, we will be able to obtain $n$ different values of $z$ and the following system of equation can be written: 
$$b\cdot z_1=0$$
$$b\cdot z_2=0$$
$$...$$
$$b\cdot z_n=0$$ 
From which $b$ can be determined, for example, by Gaussian elimination. 

<div class="alert alert-block alert-warning">
    
**Exercise** Implement Simon's algorithm for $n = 2$ and $b = 11$
    
</div>

Two n-qubit input registers are initialized to the zero state: 
$$ |\psi_1 \rangle = |0\rangle ^{\otimes n}|0\rangle ^{\otimes n} = |00\rangle_1 |00\rangle_2 $$

 Apply a Hadamard transform to the first register: 
 $$ |\psi_2 \rangle = \frac{1}{\sqrt{2^n}} \sum _{x \in \{0,1\}^n } |x\rangle|0\rangle ^{\otimes n}$$
 
 $$\frac{1}{\sqrt{2}} ( |00\rangle_1 + | 01\rangle_1 + |10\rangle_1 + |11\rangle_1 )|00\rangle_2$$

Appy oracle:
 $$ |\psi_3 \rangle = \frac{1}{\sqrt{2^n}} \sum _{x \in \{0,1\}^n } |x\rangle|f(x)\rangle $$
 
 
 $$\frac{1}{2} ( |00\rangle_1| 00\rangle_2 + | 10\rangle_1 |11\rangle_2 + |10\rangle_1|11\rangle_2 +| 11\rangle |00\rangle_2)$$

Measure the second register. 

$$ |\psi_4 \rangle = \frac{1}{\sqrt{2}}(|x\rangle + |y\rangle )$$

For instance, if the measument is $11$ then:
 $$\frac{1}{\sqrt{2}} ( |01 \rangle_1 + |10 \rangle_1)$$

Measuring the first register

$$(-1)^{x \cdot z} = (-1)^{y \cdot z}$$

**References**
* [Qiskit Simon's Algorithm](https://learn.qiskit.org/course/ch-algorithms/simons-algorithm)
* [Lecture by Peter Young](https://young.physics.ucsc.edu/150/simon.pdf)
* [Simon's Paper](https://epubs.siam.org/doi/10.1137/S0097539796298637)

## 3. The Algorithms so far <a id='alg'></a>

### Deutsch-Jozsa Algorithm
* Classical computers 
    * For some inputs, it may take **exponential time** to solve with certainty.
        * Exact classical query complexity: $2^{n-1}+1$
    * However, BPP algorithms can solve de DJ problem in **polinomial time (P)**, with a **small probability of errors**.
        * Bounded error classical query complexity:$O(1)$
    
* Quantum computers
    * Solves the problem with certainty in **quantum polynomial time (QP)**.
        * Exact quantum query complexity: $1$
    
![DJ](https://qiskit.org/textbook/ch-algorithms/images/deutsch_steps.png)

### Bernstein-Vazirani Algorithm
* The goal of this algorithm was to prove **oracle separation between complexity classes BPP (bounded-error probabilistic polynomial time) and BQP (bounded-error quantum polynomial time).**
    * Exact classical query complexity: $n$
    * Bounded error classical query complexity: $\Omega(n)$
    * Exact quantum query complexity: $1$

![BV](https://qiskit.org/textbook/ch-algorithms/images/bv1.png)

### Simon's Algorithm
* The oracle separation between classes BPP and BQP, but in this case, the separation is **exponential**.
    * Bounded error classical query complexity: $\Omega(2^{n/2})$
    * Bounded error quantum query complexity: $O(n)$

![Simon](https://qiskit.org/textbook/ch-algorithms/images/simon_steps.png)

**Refs**
* [Quantum computing slides](https://www.slideserve.com/huela/csep-590tv-quantum-computing)

## 4. Noise model <a id='em'></a>

First create a **nose model**.

In [ ]:
import qiskit_ibm_provider.jupyter  

from qiskit.providers.aer.noise import NoiseModel
from qiskit.providers.aer.noise.errors import pauli_error, depolarizing_error

In [ ]:
provider = IBMProvider()

In [ ]:
%ibm_quantum_dashboard

In [ ]:
backend = provider.get_backend('ibm_brisbane')
noise_model = NoiseModel.from_backend(backend)
print(noise_model)

In [ ]:
aer_sim = Aer.get_backend('aer_simulator')
for state in ['00','01','10','11']:
    qc = QuantumCircuit(2,2)
    if state[0]=='1':
        qc.x(1)
    if state[1]=='1':
        qc.x(0)  
    qc.measure([0, 1], [0, 1])
    t_qc = transpile(qc, aer_sim)
    qobj = assemble(t_qc)
    counts = aer_sim.run(qc, noise_model=noise_model, shots=10000).result().get_counts()
    print(state+' becomes', counts)

**Refs:**
* [Device noise simulation](https://qiskit.org/documentation/stable/0.19/tutorials/simulators/2_device_noise_simulation.html)

**Further study:**
* [Building Noise Models](https://qiskit.org/documentation/stable/0.38/tutorials/simulators/3_building_noise_models.html)